# Earthquake Signals

## Part I: Seismicity on Earth

An earthquake is a vibration of Earth caused by the sudden release of energy, usually as an abrupt breaking of rock along planar fractures called faults.  An earthquake initiates at its hypocenter or focus at some depth below the land surface or sea floor. The epicenter of the earthquake is defined as the point on the Earth’s surface above where the earthquake initiated.

But only rocks that are relatively cold and brittle (the Earth’s lithosphere) can be broken in earthquakes.  Rocks that are hot and ductile (e.g. the Earth’s asthenosphere) will deform without breaking, and therefore do not produce earthquakes. By observing where earthquakes occur, both horizontally and with depth, we can learn where stress is concentrated and infer the material properties of the Earth.

In this section, we will examine the distribution of earthquakes. You will notice that most of them are near plate boundaries. Each type of plate boundaries has a unique moving pattern shown in the image below. Keep this in mind when you look at the earthquake epicenter plot later in this section.


<img src="Images/plate_boundary_types.png" alt="drawing" width="60%"/> 

*Image: Three major types of plate boundaries.*


In [1]:
import pandas as pd
import json
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import warnings
warnings.filterwarnings('ignore')

In [ ]:
def cutoff_track(lon, lat, cutoff_lon):
    """
    Insert nan between two points that cross the cutoff lontitude. 
    Avoid horizontal line when plot the track
    
    Input Parameters:
    ----------------
    
    lon: longitude array
    lat: latitude array
    cutoff_lon: divide the curve at this cutoff longitude
    
    Return:
    ------
    
    lon, lat: updated arrays
    """
    xtrk = np.mod(lon - cutoff_lon, 360)
    is_cross = np.where(np.abs(xtrk[1:-1]-xtrk[0:-2]) > 90)[0]
    nans = np.empty(np.size(is_cross))
    nans[:] = np.nan
    lon = np.insert(lon, is_cross+1, nans)
    lat = np.insert(lat, is_cross+1, nans)
    return lon, lat

def load_plate_boundaries(filename):
    """
    Input Parameters:
    ----------------
    
    filename: input JSON file name containing the curve locations
    """    

    # Opening JSON file
    f = open(filename)

    # returns JSON object as a dictionary
    boundary = json.load(f)
    
    f.close()

    boundary = np.array(boundary[1])
    lons = boundary[:,0]
    lats = boundary[:,1]

    lons, lats = cutoff_track(lons, lats, 180)
    
    return lons, lats


def plot_earthquake_map(catalog):
    """
    Input Parameters:
    ----------------
    
    catalog: dataframe containing earthquakes
    """   
    
    rlons, rlats = load_plate_boundaries('../Geophysics/Files/ridge.json')
    tlons, tlats = load_plate_boundaries('../Geophysics/Files/transform.json')
    hlons, hlats = load_plate_boundaries('../Geophysics/Files/trench.json')

    
    fig1 = px.scatter_geo(catalog, lon="ep.lon", lat="ep.lat", size="centroid.MW", color="ep.depth", 
                     labels={"ep.lon":"longitude (degrees)", "ep.lat":"latitude (degrees)", "centroid.MW":"Moment Magnitude",
                             "ep.depth":"depth (km)", "ep.timestamp":"origin time"}, 
                     hover_data=['ep.timestamp'])

    fig1a = px.line_geo(lon=rlons, lat=rlats)
    fig1a.update_traces(line={'color':'skyblue', 'width':3})
    
    fig1b = px.line_geo(lon=tlons, lat=tlats)
    fig1b.update_traces(line={'color':'lime', 'width':3})
    
    fig1c = px.line_geo(lon=hlons, lat=hlats)
    fig1c.update_traces(line={'color':'orangered', 'width':3})
    
    fig = go.Figure(data=fig1.data + fig1a.data + fig1b.data + fig1c.data, layout = fig1.layout)
    fig.update_xaxes(range=[-180, 180], tickvals=np.arange(-180,190,30))
    fig.update_yaxes(range=[-90, 90], tickvals=np.arange(-90,100,15))
    fig.update_geos(projection_type="robinson", lataxis_showgrid=True, lonaxis_showgrid=True)
    fig.update_layout(title_text="Global CMT catalog (N = %d earthquakes)"%len(catalog), title_x=0.5)
    fig.show()

In [ ]:
# Read earthquake catalog
cmt_cat = pd.read_table("Files/Global_CMT_1972_2018.csv", delimiter=',')
cmt_cat = cmt_cat.sort_values(by=['ep.depth', 'centroid.MW'])

<div class="admonition pythonreview" name="html-admonition" style="background: lightgreen; padding: 10px">
<p class="title">Review</p>
<p>Feel free to adjust the filter parameters in the cell below to have more or less earthquakes on the map. You may hover the dots to get the information of the earthquakes. The colors of the lines indicate the type of plate boundaries: Red is a Trench, Green is a Transform, and Blue is a Ridge boundary.</p>
    </div>

In [ ]:
# Filter to improve readablility
Mw_min    = 6.5                               # Moment magnitude
Mw_max    = 10                                # Moment magnitude
depth_min = 0                                 # minimum depth in km
depth_max = 6400                              # maximum depth in km
datetime_min = '1000-01-01 00:00:00.000000'   # 'yyyy-mm-dd hh:mm:ss.SSSSSS'
datetime_max = '2050-01-01 00:00:00.000000'   # 'yyyy-mm-dd hh:mm:ss.SSSSSS'

# Don't change these two statements
mask = (cmt_cat['centroid.MW'] >= Mw_min) & (cmt_cat['centroid.MW'] <= Mw_max) & (cmt_cat['ep.depth'] >= depth_min) & (cmt_cat['ep.depth'] <= depth_max) & (cmt_cat['ep.timestamp'] >= datetime_min) & (cmt_cat['ep.timestamp'] <= datetime_max)
plot_earthquake_map(cmt_cat[mask])

**Question** Examine the regions on and around Earth’s ocean ridges and ocean trenches. Both the spatial distribution and the depths of earthquakes associated with each are different.  Describe/illustrate these differences between earthquake associated with ridges and earthquakes associated with trenches.

**Answer**:

<br/><br/>
<br/><br/>

**Question**. Using earthquake depths as evidence, discuss whether the Earth’s lithosphere is thicker at ridges or at trenches.

**Answer**:

<br/><br/>
<br/><br/>

## Part II: Seismic stations, seismographs, and seismograms


Seismographs are instruments at seismic stations that measure ground motion. The data is displayed as
seismograms. This data is of fundamental importance to the geosciences. By studying earthquake-generated ground motion we can learn about 1) the nature of the earthquake itself (the source of the motion) and 2) the material the earthquake waves travel through (Earth’s interior). This is because the observed vibration (in the time domain *t*) is the result of the effects of earthquake source, interior structure and how the instrument *senses* the vibration. These effects can be most easily modeled by considering each frequency ($\omega$) of the waveform in turn, and using their products (i.e. frequency-domain convolution per mathematical definition) to derive the waveform.

<img src = "Images/Convolution.png" width = "90%" >

*Figure: Relationship between measurement and contribution from instrument, structure and source.*



The United States Geologic Survey estimates that several million earthquakes occur each year. Many go
undetected because they hit remote areas without good seismic station coverage, or have very small
magnitudes. But various seismic networks locate something like 20,000 earthquakes a year. We will focus on two large earthquakes since they caused the whole Earth to ring like a bell, causing waveforms to be recorded at various stations well above the noise level of the instrument.

**Tohoku earthquake [USGS Link](https://earthquake.usgs.gov/earthquakes/eventpage/official20110311054624120_30/executive)**

The March 11, 2011, M 9.1 Tohoku earthquake, which occurred near the northeast coast of Honshu, Japan, on the subduction zone plate boundary between the Pacific and North America plates. The location, depth (about 25 km), and focal mechanism solutions of the March 11th earthquake are consistent with the event having occurred on the subduction zone plate boundary. Modeling of the rupture of this earthquake indicates that the fault moved as much as 50–60 m, and slipped over an area approximately 400 km long (along strike) by 150 km wide (in the down-dip direction). The Japan Trench subduction zone has hosted nine events of $m_w$ 7+ since 1973. 

The focal mechanisms that are usually given to convey this configuration are a way of plotting the three dimensional fault information in two dimensions (they’re lower hemisphere [stereographic projections](http://mathworld.wolfram.com/StereographicProjection.html)). The figure below is an attempt to show how a simple block model of the first motions of 5 common types of earthquake look when projected onto a lower hemisphere, and then when the pattern on that focal sphere is projected onto the horizontal to produce a 2D focal mechanism.

<img src = "Images/focalmechs.png" width = "40%" >

*Figure: Types of faulting and their expression as focal mechanism of the earthquake.*

The [Global Centroid-Moment-Tensor (CMT) Project](https://www.globalcmt.org) has measured the moment tensors of all earthquakes with magntiudes $m_w$ 5.5+ since 1976. The CMT project has been continuously funded by the National Science Foundation since its inception. Let us read the CMT solution of the Tohoku earthquake in the *CMTSOLUTION* format, available from their webpage.

In [ ]:
import numpy as np
import os
import subprocess
from multiprocessing import Pool
import glob
import errno
import cmath
from math import atan2
import pandas as pd
import pdb
from obspy import UTCDateTime,read_events,read,read_inventory
from obspy.geodetics import gps2dist_azimuth

#########################################################

def readcmtsolution(file='CMTSOLUTION'):
    if not os.path.isfile(file): raise FileNotFoundError(errno.ENOENT, os.strerror(errno.ENOENT), file)
    cmt={}
    f = open(file,'r')
    line=f.readline().split()
    cmt['source']=line[0];cmt['iyr']=int(line[1]);cmt['imo']=int(line[2]);cmt['ida']=int(line[3])
    cmt['iho']=int(line[4]);cmt['imi']=int(line[5]);cmt['fsec']=float(line[6]);cmt['eplat']=float(line[7]
)
    cmt['eplong']=float(line[8]);cmt['depth']=float(line[9]);cmt['mb']=float(line[10]);cmt['ms']=float(line[11])
    cmt['region']=' '.join(line[12:])

    cmt['ityphdur']=2
    cmt['itypso']=0
    cmt['time'] = UTCDateTime(cmt['iyr'],cmt['imo'],cmt['ida'],cmt['iho'],cmt['imi'],cmt['fsec'])

    # read cmts
    xm = np.zeros(6)
    while line:
        line = f.readline()
        if line[0:10] == 'event name':
            cmt['name']=line[12:].split()[0]
        elif line[0:10] == 'time shift':
            cmt['tcmt']=float(line[12:].split()[0])
        elif line[0:13] == 'half duration':
            cmt['hdur']=float(line[15:].split()[0])
        elif line[0:8] == 'latitude':
            cmt['epla']=float(line[10:].split()[0])
        elif line[0:9] == 'longitude':
            cmt['eplo']=float(line[11:].split()[0])
        elif line[0:5] == 'depth':
            cmt['depth']=float(line[7:].split()[0])
        #Double  couple
        elif line[0:3] == 'Mrr':
            xm[0]=float(line[5:].split()[0])
        elif line[0:3] == 'Mtt':
            xm[1]=float(line[5:].split()[0])
        elif line[0:3] == 'Mpp':
            xm[2]=float(line[5:].split()[0])
        elif line[0:3] == 'Mrt':
            xm[3]=float(line[5:].split()[0])
        elif line[0:3] == 'Mrp':
            xm[4]=float(line[5:].split()[0])
        elif line[0:3] == 'Mtp':
            xm[5]=float(line[5:].split()[0])
        # Single force
        elif line[0:3] == 'CFr':
            cmt['itypso']=1
            xm[1]=float(line[5:].split()[0])
        elif line[0:3] == 'CFt':
            cmt['itypso']=1
            xm[2]=float(line[5:].split()[0])
        elif line[0:3] == 'CFp':
            cmt['itypso']=1
            xm[3]=float(line[5:].split()[0])
        # Single force
        elif line[0:3] == 'SFr':
            cmt['itypso']=2
            xm[1]=float(line[5:].split()[0])
        elif line[0:3] == 'SFt':
            cmt['itypso']=2
            xm[2]=float(line[5:].split()[0])
        elif line[0:3] == 'SFp':
            cmt['itypso']=2
            xm[3]=float(line[5:].split()[0])

    if cmt['itypso'] > 1:
        xm[3]=0.
        xm[4]=0.
        xm[5]=0.
    cmt['xm']=xm
    
    # Moment tensor
    M = np.array([[xm[0], xm[3], xm[4]], [xm[3], xm[1], xm[5]], [xm[4], xm[5], xm[2]]])
    
    # Scalar moment
    M0 = np.sqrt(np.sum(M ** 2) / 2)
    cmt['m0'] = M0
    
    # Moment magnitude
    Mw = np.round(np.log10(M0) / 1.5 - 10.73, 1)
    cmt['mw'] = Mw

    return cmt

In [ ]:
# read the CMT solution file of Tohoku earthquake
cmt = readcmtsolution('Files/CMTSOLUTION_TOHOKU')
#print(cmt)

In [ ]:
from obspy.imaging.beachball import beachball
fig = beachball(cmt['xm'])

### TO DO

**Question** Based on the beachball focal mechanism above, what type of faulting caused the Tohoku earthquake? Was the fault shallowly dipping at a low angle from the surface (dip < 30$^{\circ}$) or steeply dipping at a high angle (dip > 60$^{\circ}$)? Which plate was the overriding plate?

**Answer:**

<br><br/>
<br><br/>

### Section A: Vibrations at a single station

Modern seismometers measure ground motion in three mutually perpendicular directions:

- *North-South* (LHN or BHN component). This records the north-south horizontal component of vibration.  “Up” on this graph means the ground moved north.  “Down” on this graph means the ground moved south.

- *East-West* (LHE or BHE component). This records the east-west horizontal component of vibration.  “Up” on this graph means the ground moved east.  “Down” on this graph means the ground moved west.

- *Vertical* (LHZ or BHZ component). This records the vertical component of vibration.  “Up” on this graph the means the ground moved up.  “Down” on this graph means the ground moved down. 

The prefix (L-long period, or B-broadband) indicates the sampling rate of seismic data stream. When we wish to analyse signals that are finely spaced, we use the broadband data steam (i.e. think of Nyquist frequency). Sometimes, the horizontal orientations of the sensor in the instrument are not perfectly aligned with the N-S and E-W directions, even if the vertical component is perfectly aligned. In these cases, the horizontal components are denoted as LH1 and LH2 (or BH1 and BH2). We typically analyze the motion along the propagation direction of the wavefront, which gives us clearer information on individual seismic phases (as you will see below). Note that finding the propagation direction from earthquake to a station requires the coordinates and depth of the hypocenter, as denoted by the CMT focal mechanism above. 

<img src = "Images/zrt.png" width = "45%" >

*Figure: Rotation of vibrations recorded on a seismogram to radial, transverse and vertical components along the propagation direction.*


Let us perform this calculation for the vibrations recorded on the long-period components at Ascension Island (station code: ASCN) in the South Atlantic Ocean from the Tohoku earthquake.

In [ ]:
st = read('Files/waveforms/II.ASCN.*.LH*.mseed') # Ascension Island, distance=144
print(st)

In [ ]:
#st.plot();

In [ ]:
stationdir = 'Files/stations/'
inv = read_inventory('%s%s.%s.xml' % (stationdir, st[0].stats.network, st[0].stats.station))
#inv.plot_response(0.001, output="DISP");

We also wish to focus on vibrations in the period range 20-200 seconds to start with. This done by *band-pass filtering* the seismogram below:

In [ ]:

periods = [20,200]

stat_lat = inv.select(station=st[0].stats.station)[0][0].latitude
stat_lon = inv.select(station=st[0].stats.station)[0][0].longitude
evt_lat = cmt['epla']
evt_lon = cmt['eplo']

# compute back azimuth (check sign, later!):
dist, back_az, az = gps2dist_azimuth(evt_lat, evt_lon, stat_lat, stat_lon)

# convert distance to degrees
dist = (dist / 6371000) / np.pi * 180

# select the traces from a station
st3 = st.copy()

# remove instrument response, filter, and rotate
pre_filt = [0.8/periods[1] ,1/periods[1], 1/periods[0], 1.25/periods[0]]
st3 = st3.remove_response(inventory=inv, output="DISP",pre_filt=pre_filt).taper(0.05)
if not st3.select(channel='LHE'): st3 = st3.rotate(method="->ZNE", inventory=inv,back_azimuth=back_az)
st3 = st3.rotate(method="NE->RT", inventory=inv,back_azimuth=back_az)
st3.plot();

In [ ]:
import holoviews as hv
from holoviews.operation.datashader import datashade
from holoviews.streams import PlotSize
import datashader as ds
from holoviews import opts
PlotSize.scale=2
hv.extension('plotly')

import plotly
import plotly.graph_objects as go
import plotly.express as px
plotly.offline.init_notebook_mode() 

from obspy.taup import TauPyModel
from obspy.geodetics.base import gps2dist_azimuth
import warnings
warnings.filterwarnings("ignore")

### Section B: Horizontal versus Vertical Motions

#### Task I: At a single station

In [ ]:
duration_h = 1.5
st3 = st3.slice(endtime=st3[0].stats.starttime + 3600*duration_h)

# grab the time series data for processing
scalefactor = 0.5
times = np.array([])
signals = np.array([])
component_indicator = []
components = ["T", "Z"]
for ii, component in enumerate(components):
    trace = st3.select(component=component)[0]
    t = trace.times()
    x = trace.data
    x_scale = np.max(np.abs(x)) * scalefactor
    times = np.hstack((times, t/60))       # convert to minutes
    signals = np.hstack((signals, 2*ii + x / x_scale))
    component_indicator += [component] * t.size
        
# convert to dataframe
data = dict()
cols = []

data['time (minutes)'] = times 
data['signal (normalized)'] = signals
data['component'] = component_indicator
data['station'] = ['%s-%s' % (st3[0].stats.network, st3[0].stats.station)] * times.size
data['distance'] = [dist] * times.size
data['azimuth'] = [az] * times.size
dfm = pd.DataFrame(data)

In [ ]:
fig_title = 'M%.1f %s lat=%.2f lon=%.2f dep=%.2f km band=%d-%d s station=%s-%s' % (cmt['mw'], 
                                                                                   cmt['region'].capitalize(), 
                                                                                   cmt['epla'], 
                                                                                   cmt['eplo'], 
                                                                                   cmt['depth'],
                                                                                   periods[0], 
                                                                                   periods[1],
                                                                                   st3[0].stats.network,
                                                                                   st3[0].stats.station)
fig_1 = px.line(dfm, x='time (minutes)', y='signal (normalized)', color='component', 
                hover_data={'station': ':.s', 'distance': ':.2f', 'azimuth':':.2f'}, 
                title=fig_title)
fig = go.Figure(data=fig_1,layout=fig_1.layout)
plotly.offline.iplot(fig)

#### TO DO

**Question** Identify the first seismic wave arrival at your station on the Z component. This is the first P-wave.  Note that you should consider when the seismograph first starts to respond to the P-wave – i.e., the “shoulder” of the wave, or where trace starts to climb or fall towards the first peak or trough. Report your P-wave *travel time pick* in minutes and seconds.

**Answer:**

<br><br/>
<br><br/>

**Question** Identify the first S-wave arrival at your station.  Hint: how would the relative horizontal vs. vertical motion differ for an S wave compared to a P wave?   There may also be a change in wavelength and/or amplitude; S-waves look ‘different” than P-waves. 
But there is likely more uncertainty about when to “pick” the arrival time of the first S-wave. This is because by this time, the station is still responding to the passage of P and other waves; and the S-waves are superimposed on these other waves.  This is part of the “art” of seismology – and also partly why we use data from many stations to analyze seismic waves. Report your S-wave *travel time pick* in minutes and seconds.

**Answer:**

<br><br/>
<br><br/>

**Question** Identify the surface waves on the seismogram. These are the waves with the strongest vibrations (largest amplitudes). Provide your *travel time picks* for the Rayleigh and Love wave packets on Z and T components, respectively. *Note*: Picking a travel time of a surface wave is complicated and depends strongly on the frequency of the surface wave, due to a property called *dispersion*. For this task, simply report the time of the first shoulder from the left (earliest in time). Which of the two waves (Love or Rayleigh) is arriving sooner at the station?

**Answer:**

<br><br/>
<br><br/>

#### Task II: Record Section of the USArray Transportable Array

A single seismometer can give us some information about the earthquake and interior structure. In fact, this is the idea behind deploying a seismometer on the Moon and Mars. However, *arrays* of seismometer can provide unprecedented insights into geological processes.  

[USArray](http://www.usarray.org) is a 15-year program to place a dense network of permanent and portable seismographs across the continental United States. The seismographs record local, regional, and distant (teleseismic) earthquakes. This mega-project is funded by the US National Science Foundation and we will use data from a part of this project called the *Transportable Array*.


<img src = "Images/Install_plan_2014.png" width = "70%" >

*Figure: Installation plan of the transportable array of USArray.*

USArray has a large traveling network of 400 high-quality, portable seismographs that are being placed in temporary sites across the United States in a rolling fashion. Station spacing is ~70 km (42 mi). Transportable Array data are extremely useful for mapping the structure of Earth's uppermost 70 km. The array was initially deployed in the westernmost United States. Unless adopted and made into a permanent installation, after 18-24 months, each instrument is picked up and moved to the next carefully spaced array location to the east. When completed, over 2000 locations will have been occupied during this program.

Note that since we are looking at the data from Tohoku earthquake in 2011, we are using data from the Transportable Array as it was installed at that time. This means the stations that we are analyzing lie on a grid from Michigan to Louisiana.


In [ ]:
from scipy import interpolate

def plottraces(cmt, 
               st, 
               stationdir, 
               periods=[20,100],
               component="T", 
               phaselist=["P", "S", "PcP", "ScS"],
               plottype="holoviews",
               duration_h=1.0,
               scalefactor=1.0):
    '''
    Make holoview objects for plotting traces against epicentral distance
    
    Input:
    -----
    cmt:            CMT Solution
    st:             Obspy stream object containing 3 components seismograms
    stationdir:     directory to station XML files for the streams
    periods:        [min, max] periods for bandpass filter
    phaselist:      list of phases to be plotted
    plottype:       either "holoviews" or "datashader"
    duration:       the number of hours of seismograms to be plotted
    scalefactor:    factor to reduce the amplitude of the seismogram
    
    Output:
    ------
    overlay_trace:  holoview object for trace plots
    overlay_phase:  holoview object for phase plots
    options:        options used by datashader
    
    These outputs will be used in the next command to create a plot:
    ---------------------------------------------------------------
    datashade(ndoverlay * overlay_phase, cmap=["black"], cnorm='linear', 
              aggregator=ds.count(), line_width=8).opts(opts)
    
    '''
        
    ########################################################
    # READ, PREOCESS, AND GATHER TRACES
    ########################################################
    signals = []
    dists = []

    # set the time for all trace to be the same
    t_trace = st[0].slice(endtime=st[0].stats.starttime + 3600*duration_h).times()

    for tr in st.select(channel='LHZ'):
        inv = read_inventory('%s%s.%s.xml' % (stationdir, tr.stats.network, tr.stats.station))
        stat_lat = inv.select(station=tr.stats.station)[0][0].latitude
        stat_lon = inv.select(station=tr.stats.station)[0][0].longitude
        evt_lat = cmt['epla']
        evt_lon = cmt['eplo']

        # compute back azimuth (check sign, later!):
        dist, back_az, _ = gps2dist_azimuth(evt_lat, evt_lon, stat_lat, stat_lon)

        # convert distance to degrees
        dist = (dist / 6371000) / np.pi * 180
        dists += [dist]

        # select the traces from a station
        st3 = st.select(station=tr.stats.station).copy()

        # remove instrument response, filter, and rotate
        pre_filt = [0.8/periods[1] ,1/periods[1], 1/periods[0], 1.25/periods[0]]
        st3 = st3.slice(endtime=st3[0].stats.starttime + 3600*duration_h).remove_response(inventory=inv, 
                            output="DISP",pre_filt=pre_filt).taper(0.05)
        if not st3.select(channel='LHE'):
            st3 = st3.rotate(method="->ZNE", inventory=inv,back_azimuth=back_az)
        st3 = st3.rotate(method="NE->RT", inventory=inv,back_azimuth=back_az)

        # grab the time series data for processing
        trace = st3.select(component=component)[0]
        t = trace.times()
        x = trace.data

        # interpolate to the same time
        f = interpolate.interp1d(t, x, kind='linear', fill_value='extrapolate')
        x = f(t_trace)
        x_scale = np.max(np.abs(x)) * scalefactor
        signals += [dist + x / x_scale]
        
        
    # convert to dataframe
    data = dict()
    cols = []

    for ii in range(len(signals)):
        data["trace_%03d" % ii] = signals[ii]
        cols += ["trace_%03d" % ii]
    data['time'] = t / 60                                 # convert to minutes
    dfm = pd.DataFrame(data)
        
    ########################################################
    # CALCULATE TRAVEL TIMES
    ########################################################
    dist_min = np.min(dists)
    dist_max = np.max(dists)

    distances = np.arange(np.floor(dist_min), np.ceil(dist_max) + 1, 0.5)
    traveltime_phases = np.ones((np.size(distances), len(phaselist))) * np.nan

    model = TauPyModel(model="ak135")
    for ii, dist in enumerate(distances):
        for jj, phase in enumerate(phaselist):
            arrivals = model.get_travel_times(source_depth_in_km=cmt['depth'],
                                              distance_in_degree=dist,
                                              phase_list=[phase])
            if arrivals:
                traveltime_phases[ii, jj] = arrivals[0].time
                
    # convert to dataframe
    traveltime = dict()
    for jj, phase in enumerate(phaselist):
        traveltime[phase] = traveltime_phases[:,jj] / 60  # convert to minutes
    traveltime['distance'] = distances
    dft = pd.DataFrame(traveltime)
    
    ########################################################
    # PLOT
    ########################################################
    options = hv.opts.RGB(width=800, height=800, xlabel='Time (minutes)', 
                       title='M%.1f %s lat=%.2f lon=%.2f dep=%.2f km comp=%s band=%d-%d s, phase=%s' % (cmt['mw'], 
                                                                                                        cmt['region'].capitalize(), 
                                                                                                        cmt['epla'], 
                                                                                                        cmt['eplo'], 
                                                                                                        cmt['depth'], 
                                                                                                        component, 
                                                                                                        periods[0], 
                                                                                                        periods[1],
                                                                                                        phaselist))
    
    
    if plottype == "datashader":
        overlay_trace = hv.NdOverlay({c:hv.Curve((dfm['time'], dfm[c]), vdims = ['Distance (degree)'], label='trace') for c in cols})
        if len(phaselist) > 0: 
            overlay_phase = hv.NdOverlay({phase:hv.Curve((dft[phase], dft['distance']), 
                                                     vdims = ['Distance (degree)']
                                                     #label = phase
                                                    ) for phase in phaselist})
            # Make the phase curve thicker
            overlay_phase = overlay_phase * overlay_phase * overlay_phase * overlay_phase
        else:
            overlay_phase=None
    else:
        overlay_trace = [hv.Curve((dfm['time'], dfm[c]), vdims = ['Distance (degree)'], group='trace') for c in cols]
        if len(phaselist) > 0: 
            overlay_phase = [hv.Curve((dft[phase], dft['distance']), vdims = ['Distance (degree)'], group = 'phase') for phase in phaselist]
        else:
            overlay_phase=None
    
    return overlay_trace, overlay_phase, options

In [ ]:
# read waveforms recorded by US Transportable Array
st = read('Files/waveforms/TA.*.LH*.mseed')

In [ ]:
#overlay_trace, overlay_phase, options = plottraces(cmt, st, 'Files/stations/', [20,200], "Z", ["S", "pP", "P","PP"], "datashader")
overlay_trace, overlay_phase, options = plottraces(cmt, st, 'Files/stations/', [20,200], "Z", [], "datashader")
if overlay_phase != None:
    things_to_plot = overlay_trace * overlay_phase
else:
    things_to_plot = overlay_trace 
datashade(things_to_plot, cmap="gist_gray", cnorm='linear', aggregator=ds.count()).opts(options)

In [ ]:
#overlay_trace, overlay_phase, options = plottraces(cmt, st, 'Files/stations/', [20,100], "T", ["S", "ScS"], "datashader", 1, 2)
overlay_trace, overlay_phase, options = plottraces(cmt, st, 'Files/stations/', [20,100], "T", [], "datashader", 1, 2)
if overlay_phase != None:
    things_to_plot = overlay_trace * overlay_phase
else:
    things_to_plot = overlay_trace 
datashade(things_to_plot, cmap="gist_gray", cnorm='linear', aggregator=ds.count()).opts(options)

#### TO DO

**Question** The *record sections* above show data from the first hour after the earthquake origin time on the Z and T components. Zoom into any distance range 10 degrees in width, and download the image as png from the options (top right). Draw a line with a red pen where you see the P wave (on the Z component) and S wave (on the T component). Find slope of this curve and report this as the speed of the P and S wave (in m/s). Are the slopes expected to vary with distance? If so, why? *Hint:* You can assume that 1 degree equals 111.1949 km on average. Attach the annotated image with the assignment.

**Answer:**

<br><br/>
<br><br/>

### Part 2: Waveforms at different period bands

Next, we will evaluate if we can glean more information by analyzing waveforms at other period bands. As you will see, there is a plethora of information in these seismograms at various period/frequency bands. Let us look at the vertical (Z) component from the US Transportable Array at two period bands (5-40 seconds vs 20-100 seconds).

In [ ]:
overlay_trace, overlay_phase, options = plottraces(cmt, st, 'Files/stations/', [5,40], "Z", [], "datashader", 1, 2)
if overlay_phase != None:
    things_to_plot = overlay_trace * overlay_phase
else:
    things_to_plot = overlay_trace 
datashade(things_to_plot, cmap="gist_gray", cnorm='linear', aggregator=ds.count()).opts(options)

In [ ]:
overlay_trace, overlay_phase, options = plottraces(cmt, st, 'Files/stations/', [20,100], "Z", [], "datashader", 1, 2)
if overlay_phase != None:
    things_to_plot = overlay_trace * overlay_phase
else:
    things_to_plot = overlay_trace 
datashade(things_to_plot, cmap="gist_gray", cnorm='linear', aggregator=ds.count()).opts(options)

#### TO DO

**Question** The *record sections* above show data from the first hour after the earthquake origin time on the Z component for data filtered at two period bands (5-40 seconds vs 20-100 seconds). Do you see any phases that are more prominent in one period band or the other? Annotate this phase by zooming into any distance range 10 degrees in width, and downloading the image as png from the options (top right). Attach the annotated image with the assignment.

**Answer:**

<br><br/>
<br><br/>

### Part 3: Spectrum of Vibrations


In [ ]:
%matplotlib inline

from scipy.fftpack import fft
import numpy as np
from importlib import reload
import os
from scipy import signal
import matplotlib.pyplot as plt

To complete the illustration of time versus frequency plots (a normal signal versus it's spectrum), here is a seismic signal (ground motion caused by an earthquake). The time series is a complicated looking signal. In fact, this signal can be described as a combination of a very large number of sinusoids, all with amplitudes as shown in the spectrum graph.

**2004 Sumatra - Andaman Islands Earthquake [USGS Link](https://earthquake.usgs.gov/earthquakes/eventpage/official20041226005853450_30/executive)**

The devastating M 9.1 earthquake off the west coast of northern Sumatra on December 26, 2004, occurred as the result of thrust faulting on the interface of the India plate and the Burma microplate. In a period of minutes, the faulting released elastic strains that had accumulated for centuries from ongoing subduction of the India plate beneath the overriding Burma microplate. 

Since this earthquake was so large, it was able to *ring* the Earth like a bell, causing vibrational normal modes or standing waves. Let us look at the data from this earthquake recorded at Echery - Sainte Marie aux Mines, France.


In [ ]:
from pathlib import Path
import numpy as np
import matplotlib.pyplot as plt
from obspy.clients.fdsn import Client
from obspy import UTCDateTime,read_inventory, read
from obspy.geodetics.base import gps2dist_azimuth
from gatspy.periodic import LombScargleFast

inventory_store = 'Files/ECH_inventory.xml'
path = Path(inventory_store)

if path.is_file():
    inv = read_inventory(inventory_store)
else:
    # Create two times which we will later use to download time series data.
    starttime = UTCDateTime(2004, 12, 26, 0, 58, 50)
    # Create a new time object by adding 10 days to the previous ones. Time
    # differences are in seconds.
    endtime = starttime + 86400 * 10
    client='IRIS'
    level='response'
    query ='G-ECH-*-LH*'

    c = Client(client)
    network,station,location,channel=query.split('-')
    inv = c.get_stations(network=network, station=station, location=location, channel=channel,
                     starttime=starttime, endtime=endtime,level=level)
    
    inv.write(inventory_store, format='STATIONXML')  

In [ ]:
st = read('Files/Sumatra_2004_ECH.mseed')

In [ ]:
nhours = 230
pre_filt=[1e-4,2e-4,3e-3,4e-3]

# read stat_lon, stat_lat
stat_lon = inv[0][0].longitude
stat_lat = inv[0][0].latitude

# read evt_lat, evt_lon
evt_lat = 3.09
evt_lon = 94.26

# compute back azimuth (check sign, later!):
dist, back_az, _ = gps2dist_azimuth(evt_lat, evt_lon,stat_lat, stat_lon)        

st2 = st.copy().slice(endtime=st[0].stats.starttime + 3600*nhours).remove_response(inventory=inv, output="ACC",pre_filt=pre_filt).rotate(method="NE->RT", inventory=inv,back_azimuth=back_az).taper(0.05)

# Remember the copy()!
tr = st2.select(component="Z")[0]


fmin = 0.0001
fmax = 0.001
N = 100000 # frequency resolution
df = (fmax - fmin) / N

time = np.linspace(start=0,stop=tr.stats.endtime-tr.stats.starttime,num=tr.stats.npts,endpoint=True)
model = LombScargleFast().fit(time, tr.data)
power = model.score_frequency_grid(fmin, df, N)
freqs = fmin + df * np.arange(N)

In [ ]:
# convert to dataframe
data = dict()
data['Frequency [mHz]'] = freqs*1000 
data['Power'] = power
dfm = pd.DataFrame(data)


fig_title = 'Station = %s-%s, %s Channel' % (tr.stats.network,tr.stats.station,tr.stats.channel)
fig_1 = px.line(dfm, x='Frequency [mHz]', y='Power', 
                title=fig_title)
fig = go.Figure(data=fig_1,layout=fig_1.layout)
plotly.offline.iplot(fig)

#### TO DO

**Question** Report the approximate frequencies that you observe on the spectrum here. Identify the lowest frequency (longest period) normal mode and describe how it deforms the Earth.

**Answer:**

<br><br/>
<br><br/>

In [ ]:
# LOOK AT TIDES
fmin = 0.001*1E-3
fmax = 0.03*1E-3

pre_filt=[1e-6,2e-6,3e-3,4e-3]
st2 = st.copy().slice(endtime=st[0].stats.starttime + 3600*nhours).remove_response(inventory=inv, 
                      output="ACC",pre_filt=pre_filt).rotate(method="NE->RT", 
                      inventory=inv,back_azimuth=back_az).taper(0.05)
tr = st2.select(component="Z")[0]
tr.plot()

N = 60 # frequency resolution
df = (fmax - fmin) / N

# Faster
time = np.linspace(start=0,stop=tr.stats.endtime-tr.stats.starttime,num=tr.stats.npts,endpoint=True)
model = LombScargleFast().fit(time, tr.data)
power = model.score_frequency_grid(fmin, df, N)
freqs = fmin + df * np.arange(N)

In [ ]:
# convert to dataframe
data = dict()
data['Frequency [mHz]'] = freqs*1000 
data['Power'] = power
dfm = pd.DataFrame(data)


fig_title = 'Station = %s-%s, %s Channel' % (tr.stats.network,tr.stats.station,tr.stats.channel)
fig_1 = px.line(dfm, x='Frequency [mHz]', y='Power', 
                title=fig_title)
fig = go.Figure(data=fig_1,layout=fig_1.layout)
plotly.offline.iplot(fig)

#### TO DO

**Question** Seismometer are so sensitive that they also record vibrations due to tides in the solid Earth. An example is seen in the spectrum above. Report the two frequencies. Convert to minutes/hours and comment on the forces causing these longer period vibrations (compared to seismic waves).

**Answer:**

<br><br/>
<br><br/>